In [1]:
import pandas as pd
import request
import re
import numpy as np
import requests
import regex
from bs4 import BeautifulSoup
from selenium import webdriver
import time

In [2]:
from time import sleep

In [3]:
pd.set_option("max_rows", 300)

In [4]:
p =re.compile('>[0-9]<') # 전체로 re.compile 만들어두고 

In [15]:
day = input('Enter the date you want to Crawling : ')
DB_temp = pd.DataFrame(np.arange(12).reshape(1,-1),columns= ['num', 'title','time','company','good','hunhun','sad','angry','want','dat','link','article'])
globals()['News_{}'.format(day)] = DB_temp
page_select = 'https://news.naver.com/main/list.nhn?mode=LS2D&sid2=731&mid=shm&sid1=105&date='+str(day) #str 제거
page = requests.get(page_select)
page_soup = BeautifulSoup(page.text, 'lxml')
page_that = page_soup.select('#main_content > div.paging')
pp = p.findall(str(page_that[0]))
page_num = int(pp[-1][1])

site_name = []
for i in range(page_num) : 
    site_name.append(page_select+"&page="+str(i+1))
    
sitelist_sum = []
for i in range(len(site_name)):
    listsoup = requests.get(site_name[i])
    Blistsoup = BeautifulSoup(listsoup.text, 'lxml')
    sitelist2 = Blistsoup.select('#main_content > div.list_body.newsflash_body > ul.type06_headline > li > dl > dt > a')
    sitelist1 = Blistsoup.select('#main_content > div.list_body.newsflash_body > ul.type06 > li> dl > dt > a')
    sitelist = sitelist2+sitelist1
    sitelist_real = [a['href'] for a in sitelist]
    sitelist_sum = sitelist_sum + sitelist_real
    sitelist_sum = list(set(sitelist_sum))
    
len(sitelist_sum)

#sitelist_sum 이 우리가 원하는 날에 있는 모든 기사의 하이퍼링크 모음

Enter the date you want to Crawling : 20191030


92

In [ ]:
sitelist_sum

In [ ]:
News_20191029

In [16]:
for i in sitelist_sum :
    driver = webdriver.Chrome('chromedriver')
    base_url = i
    driver.get(base_url)
    sleep(3)
    soup = BeautifulSoup(driver.page_source, "lxml")
    
    
    good2 = soup.select('#spiLayer > div._reactionModule.u_likeit > ul > li.u_likeit_list.good > a > span.u_likeit_list_count._count')
    good = [item.get_text().strip() for item in good2]
    hunhun2 = soup.select('#spiLayer > div._reactionModule.u_likeit > ul > li.u_likeit_list.warm > a > span.u_likeit_list_count._count')
    hunhun = [item.get_text().strip() for item in hunhun2]
    sad2 = soup.select('#spiLayer > div._reactionModule.u_likeit > ul > li.u_likeit_list.sad > a > span.u_likeit_list_count._count')
    sad = [item.get_text().strip() for item in sad2]
    angry2 = soup.select('#spiLayer > div._reactionModule.u_likeit > ul > li.u_likeit_list.angry > a > span.u_likeit_list_count._count')
    angry = [item.get_text().strip() for item in angry2]
    want2 = soup.select('#spiLayer > div._reactionModule.u_likeit > ul > li.u_likeit_list.want > a > span.u_likeit_list_count._count')
    want = [item.get_text().strip() for item in want2]
    dat2 = soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_head > a > span.u_cbox_count')
    dat = [item.get_text().strip() for item in dat2]
    
    
    ex = requests.get(i)
    exsoup = BeautifulSoup(ex.text,'lxml')
    
    
    head2 = exsoup.select("#articleTitle")
    head = [item.get_text().strip() for item in head2]
    company2 = exsoup.select("#main_content > div.article_header > div.press_logo > a > img")
    company = [img["alt"] for img in company2]
    time2 = exsoup.select('#main_content > div.article_header > div.article_info > div > span')
    time = [item.get_text().strip() for item in time2]
    article2 = exsoup.select('#articleBodyContents')
    article = [item.get_text().strip() for item in article2]
    link = i
    
    
    
    empty=[0,0,0,0,0,0,0,0,0,0,0,0]
    empty[0] = 0
    empty[1] = head[0]
    empty[2] = time[0]
    empty[3] = company[0]
    empty[11] = article[0][64:]
    empty[4] = good[0]
    empty[5] = hunhun[0]
    empty[6] = sad[0]
    empty[7] = angry[0]
    empty[8] = want[0]
    #empty[9] = dat[0]
    empty[10] = i
    empty = np.array(empty).T
    df = pd.DataFrame(empty).T
    df.columns =['num', 'title','time','company','good','hunhun','sad','angry','want','dat','link','article']
    globals()['News_{}'.format(day)] = globals()['News_{}'.format(day)].append(df, ignore_index = True)
News_20191030

num                                              title  \
0    0                                                  1   
1    0           LG전자, 3분기 스마트폰 18분기째 적자…5G폰 올인, 성과 ‘미지수’   
2    0              "두번째 폴드는 위 아래로 접는다" 삼성전자 새 폴더블 콘셉트 공개   
3    0                        한국철도 "전화번호 인증하고 경품도 받아 가세요"   
4    0                      '폴더블·8K·AI'…삼성, 애플 안방서 미래 펼쳤다   
5    0                삼성전자, IBM과 협업 美서 응급요원 실시간 건강 감시 서비스   
6    0            삼성전자, 美실리콘밸리서 '개발자대회'…갤럭시 새 UX 등 선봬(종합)   
7    0              적자 절반으로 줄인 LG폰…"5G 중가폰 내고 ODM 확대"(종합)   
8    0             “ODM 생산 저가 중심에서 중가 모델까지 확대할 것”-LG전자 컨콜   
9    0       [2보] LG전자 3분기 영업익 4.4% 증가한 7천814억원…10년 만에 최대   
10   0                   LGU+, '우리동네 멤버십' 출시…골목 매장 마케팅 지원   
11   0                  SK㈜ C&C, 남아공 ‘바이탈리티’ 플랫폼 개발 사업 수주   
12   0                 고동진 삼성전자 사장 “끊김없는 모바일 경험 위해 혁신 지속”   
13   0                      "5G·IoT로 초정밀 골프"…SKT-브이씨 업무협약   
14   0           LG전자 3분기 영업이익 10년 만에 최대…'생활가전·TV 선전'(종합)   
15   0         [SDC 19] 삼성, IBM과 파트너십 강화…5G·AI 모바일 솔루션 발표   
16   0                  웨스턴디지털, 슬림형 외장하드 '마이 패스포트' 신제품 출시   
17   0                      SK텔레콤, 금리 최대 연 5% 주는 적금 2탄 출시   
18   0                 LG 생활가전 잇단 '신기록'…스마트폰 적자 대폭 축소(종합)   
19   0                  LG 폰, 5G 선점·ODM 확대로 '2020 부활' 꾀한다   
20   0                    애플 에어팟 프로 써 보니…"노이즈 캔슬링 제대로 작동"   
21   0                   [SDC19] 삼성 스마트싱스, IoT 허브까지 연동 확대   
22   0                    데일리호텔, '특1급 호텔' 거래액 월평균 50% 늘었다   
23   0                   [포토무비] '좋아요' 수가 적으면 우울…혹시 포모증후군?   
24   0                  LG전자 스마트폰, 3Q 적자 줄였지만 4Q 다시 ‘먹구름’   
25   0                          삼성전자, 가로로 접는 폴더블폰 새 버전 공개   
26   0                      [LG전자컨콜] 스마트폰 ODM 확대, ‘저가→중가’   
27   0                 네이버 실시간 검색어 일부 개편…같은 연령대 관심사 먼저 표출   
28   0                        샤오미, 에릭슨과 '특허戰' 종료…인도 본격 공략   
29   0                  삼성전자, 가로로 반 접히는 새로운 형태 폴더블스마트폰 공개   
30   0               삼성 갤S10, 이번엔 SW 베타 업데이트 시 잠금해제 안돼 논란   
31   0                   삼성전자, 美서 ‘개발자 콘퍼런스’ 개최…차세대 UX 공개   
32   0              스타트업 “낡은 규제에 사면초가”… 택시업계 “타다 즉시 중단해야”   
33   0                 네이버, 10월 31일부터 '실검 순위' 연령대로 개편해 제공   
34   0                   “5G폰 내년도에도 순익에 큰 도움 될 것”-LG전자 컨콜   
35   0             [영상] "갤폴드는 시작에 불과"…삼성, 가로로 접히는 폴더블폰 공개   
36   0                       인기 경력자?…"SKY 출신 경력 10년차 개발자"   
37   0                     LG 생활가전 잇단 '신기록'…스마트폰 적자 대폭 축소   
38   0              [영상] “AI 탑재한 수도꼭지가 백만 원?”…콜러 스마트 수도꼭지   
39   0  [스포츠서울 소비자선호도1위브랜드대상 : 음악할래]음악교육분야 혁신적인 음악 서비스...   
40   0                SKT, 최대 연 5% 금리 주는 'T 하이5적금' 시즌2 출시   
41   0                퀄컴, LG전자와 차량용 인포테인먼트 '웹OS 오토' 개발 협력   
42   0                  "5G 이용자 4명중 3명꼴로 '불만'…이용지역 너무 협소"   
43   0                KT AI로 이루는 꿈, “영어동화책 유창하게 읽어주고 싶어요”   
44   0              삼성 새UX '원 UI 2'…스마트폰 한손 조작·시각적 편안함 강조   
45   0                  삼성전자, SDC2019 개최…가로로 접는 새 폴더블폰 공개   
46   0                     세종시에서 실전 주행한 자율주행 버스…승하차도 '거뜬'   
47   0                    삼성 '원 UI 2' 베일 벗었다…"갤럭시 접근성 강화"   
48   0                     SK텔레콤-브이씨, 5G 초정밀골프 ICT 업무 협약식   
49   0                  "5G·원가절감 通했다"…LG 폰, 적자폭 1천500억 감소   
50   0                    LG전자 "올레드, 고가 프리미엄 TV 시장 장악할 것"   
51   0                      엔비디아, 지포스 GTX 1660·1650 슈퍼 공개   
52   0                  이번엔 클램셸 디자인 폴더블폰…뜨거워지는 스마트폰 접기 경쟁   
53   0                 [SDC19] 삼성전자, 인텔과 공동 설계한 노트북 3종 공개   
54   0              [SDC 19] 삼성전자, 사용자 경험 강화한 `원 UI 2` 공개   
55   0                   LG전자 "건조기 논란, 소비자보호원 권고안 충실히 이행"   
56   0              삼성전자, 가로로 반 접히는 새로운 형태 폴더블스마트폰 공개(종합)   
57   0               삼성전자, 가로로 접히는 폴더블폰 공개 …“갤폴드는 시작에 불과”   
58   0                  오픈뱅킹 써봤더니…"은행 앱, 하나만 남기고 지워도 되겠네"   
59   0            "삼성과 함께 모바일 시장 열자" IBM·인텔, SDC19서 협업 발표   
60   0                [컨콜] LG전자, 듀얼스크린 5G폰으로 모바일 흑자전환 노린다   
61   0      “올해 스마트폰 매출 정체, 주력 시장 美·韓 시장 감소 요인 커”-LG전자 컨콜   
62   0                  LG전자, 3Q 휴대폰 적자 1612억… 2Q '절반' 수준   
63   0                    LG 3분기 스마트폰 적자 절반 줄였다…베트남 이전 효과   
64   0                       LG 스마트폰, 

In [ ]:
News_20191029

In [17]:
globals()['News_{}'.format(day)].to_csv('News_20191030.csv',index = False, encoding='utf-8-sig')

댓글 크롤링 양식

In [18]:
sitelist_comment = []
for i in range(len(sitelist_sum)):
    sitelist_comment_temp = sitelist_sum[i][:37] + 'm_view=1&includeAllCount=true&' + sitelist_sum[i][38:]
    sitelist_comment.append(sitelist_comment_temp)
sitelist_comment

['https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=138&aid=0002078915',
 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=014&aid=0004318595',
 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=001&aid=0011178663',
 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=092&aid=0002173567',
 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=001&aid=0011176991',
 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=001&aid=0011177410',
 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=001&aid=0011179252',
 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&si

In [7]:
p1 = re.compile('<span class="u_cbox_nick">.*</span></span></span></span></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap">')
p2 = re.compile('ass="u_cbox_contents" data-lang="ko">.*</span></div><div class="u_cbox_info_base"><span class="u_cbox_date"')
p22= re.compile('<span class="u_cbox_delete_contents">.*</span></div><div class="u_cbox_info_base"><span class="u_cbox_date"')
p3 = re.compile('0900">.*</span><span class=')
p4 = re.compile('<strong class="u_cbox_reply_txt">답글</strong><span class="u_cbox_reply')
p55 = re.compile('ass="u_cbox_reply_cnt">.*</span></a><div class=')
p5 = re.compile('u_cbox_reply_cnt u_vc">.*</span></a><div class=')
p6 = re.compile('<strong class="u_vc">공감/비공감</strong>')
p7 = re.compile('<em class="u_cbox_cnt_recomm">.*</em></a><a class="u_cbox_btn_unrecomm')
p8 = re.compile('비공감</span><em class="u_cbox_cnt_unrecomm">.*</em></a></div></div><span class="u_cbox_comm')
c = re.compile('>\S+\W+<')

In [ ]:
com_url = 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&mode=LSD&mid=shm&sid1=105&oid=020&aid=0003244860'

In [19]:
comm_df= pd.DataFrame(np.arange(7).reshape(1,-1))
for com_url in sitelist_comment :
    driver = webdriver.Chrome('chromedriver')
    driver.get(com_url)
    sleep(3)
    com_soup = BeautifulSoup(driver.page_source, "lxml")
    comment_many_temp = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_head > a > span.u_cbox_count') + com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_head > a > span.u_cbox_count')
    comment_many = int(str(comment_many_temp[0])[27:-7])
    for i in range(int((comment_many-1)/20)):
        driver.find_element_by_css_selector("#cbox_module > div > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()
        sleep(2)
    com_soup = BeautifulSoup(driver.page_source, "lxml")
    
    aa = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box')
    print(aa)
    comm_df
    for i in aa :
        templist = [0,0,0,0,0,0,0]
        templist[0] = c.findall(str(i))[0][1:-1] 
        templist[1] = (p2.findall(str(i))+ p22.findall(str(i)))[0][37:-68]
        templist[2] = p3.findall(str(i))[0][6:26]
        if p4.findall(str(i)) != []:
            templist[3] = (p55.findall(str(i)) + p5.findall(str(i)))[0][23:-22]

        else :
            templist[3] = 'Nan'
        if p6.findall(str(i)) != []:
            templist[4] = p7.findall(str(i))[0][30:-38]
            templist[5] = p8.findall(str(i))[0][42:-45]
        else:
            templist[4] = 'Nan'
            templist[5] = 'Nan'
        templist[6] = com_url
        templist = np.array(templist)
        templist = pd.DataFrame(templist).T
        comm_df =comm_df.append(templist)
    
comm_df.to_csv('Com_20191030.csv',index = False, encoding='utf-8-sig')
comm_df

[<div class="u_cbox_comment_box"><div class="u_cbox_area"><div class="u_cbox_info"><span class="u_cbox_info_main"><span class="u_cbox_name"><span class="u_cbox_name_area"><span class="u_cbox_nick_area"><span class="u_cbox_nick">sam9****</span></span></span></span></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap"><span class="u_cbox_contents" data-lang="ko">LG 정수기 곰팡이이라고 검색해 보세요 난리도 아니에요 정수기 뚜껑 열어 어떠니 곰팡이가 산더미처럼 나와요 고객 센터에 문의했더니 자연스러운 현상이라고 의무 약정 기간 동안 의무적으로 먹으래요 환불해 달라고 했더니 절대 안 된다고 위약금을 내야지 환불이 된다고 하네요 LG를 믿었는데 건조기도 사고 치더니 이번에 정말 큰 사고를 치네요 LG가 깡패도 아니고 나쁜 놈들 너무 화나요LG 정수기 곰팡이 라고 검색해 보세요</span></div><div class="u_cbox_info_base"><span class="u_cbox_date" data-value="2019-10-30T22:56:28+0900">2019.10.30. 22:56:28</span><span class="u_cbox_work_main"><a class="u_cbox_btn_report" data-action="blindReport#open" data-log="RPC.fold" data-param="1933213195" href="#"><span class="u_cbox_ico_bar"></span><span class="u_cbox_ico_report"></span><span class="u_cbox_in_re

[]
[]
[]
[]
[<div class="u_cbox_comment_box"><div class="u_cbox_area"><div class="u_cbox_info"><span class="u_cbox_info_main"><span class="u_cbox_name"><span class="u_cbox_name_area"><span class="u_cbox_nick_area"><span class="u_cbox_nick">jyh0****</span></span></span></span><button class="u_cbox_btn_totalcomment" data-action="userComment" data-log="RPC.ulist" data-param="objectId:'news001,0011179252',commentNo:1903369843,mine:false,open:true" type="button"><span class="u_cbox_txt_total">댓글모음</span><span class="u_cbox_ico_arrow"></span></button></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap"><span class="u_cbox_contents" data-lang="ko">왜 사람들이 엘지폰을 잘 안쓰는 이유 1.중고가격 똥값2.한번 만들고 지원안되는 소프트웨어3.무한발열 4.서비스센터 불친절 플러스 망 부족5.같은 값이면 갤럭시쓰는 가격 차이임직원 모두들 아시면서....</span></div><div class="u_cbox_info_base"><span class="u_cbox_date" data-value="2019-10-30T20:05:29+0900">2019.10.30. 20:05:29</span><span class="u_cbox_work_main"><a class="u_cbox_btn_report" data-action="blin

[]
[]
[]
[]
[]
[]
[<div class="u_cbox_comment_box"><div class="u_cbox_area"><div class="u_cbox_info"><span class="u_cbox_info_main"><span class="u_cbox_name"><span class="u_cbox_name_area"><span class="u_cbox_nick_area"><span class="u_cbox_nick">p0re****</span></span></span></span></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap"><span class="u_cbox_contents" data-lang="ko">우리 집도 큰 역할 했음을..</span></div><div class="u_cbox_info_base"><span class="u_cbox_date" data-value="2019-10-30T16:42:47+0900">2019.10.30. 16:42:47</span><span class="u_cbox_work_main"><a class="u_cbox_btn_report" data-action="blindReport#open" data-log="RPC.fold" data-param="1912874882" href="#"><span class="u_cbox_ico_bar"></span><span class="u_cbox_ico_report"></span><span class="u_cbox_in_report">신고</span></a></span></div><div class="u_cbox_tool"><a class="u_cbox_btn_reply" data-action="reply#toggle" data-log="RPC.replyopen#RPC.replyclose" data-param="1912874882" href="#"><strong class=

[]
[]
[<div class="u_cbox_comment_box"><div class="u_cbox_area"><div class="u_cbox_info"><span class="u_cbox_info_main"><span class="u_cbox_name"><span class="u_cbox_name_area"><span class="u_cbox_nick_area"><span class="u_cbox_nick">kwch****</span></span></span></span></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap"><span class="u_cbox_contents" data-lang="ko">이자로 약 20*12*0.05=12 만원.. (2년 20씩 평잔 기준) 다른데서 6~7만원 받는 것에 비해 4~5만원 이득... 다른데 쓰는 사람이 옮길 수준은 아니고 이미 쓰던 사람은 가입할만 하겠네.</span></div><div class="u_cbox_info_base"><span class="u_cbox_date" data-value="2019-10-30T09:55:46+0900">2019.10.30. 09:55:46</span><span class="u_cbox_work_main"><a class="u_cbox_btn_report" data-action="blindReport#open" data-log="RPC.fold" data-param="1902808633" href="#"><span class="u_cbox_ico_bar"></span><span class="u_cbox_ico_report"></span><span class="u_cbox_in_report">신고</span></a></span></div><div class="u_cbox_tool"><a class="u_cbox_btn_reply" data-action="reply#toggle" da

[<div class="u_cbox_comment_box"><div class="u_cbox_area"><div class="u_cbox_info"><span class="u_cbox_info_main"><span class="u_cbox_name"><span class="u_cbox_name_area"><span class="u_cbox_nick_area"><span class="u_cbox_nick">go33****</span></span></span></span></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap"><span class="u_cbox_contents" data-lang="ko">엘쥐야!  요즘은 특별한 기능은 필요없고 아이폰이나 삼성폰 화웨이폰 처럼 만들면 된다. 베터리, 카메라가 좋으면 거기서 거기다.</span></div><div class="u_cbox_info_base"><span class="u_cbox_date" data-value="2019-10-31T23:56:32+0900">2019.10.31. 23:56:32</span><span class="u_cbox_work_main"><a class="u_cbox_btn_report" data-action="blindReport#open" data-log="RPC.fold" data-param="1955969994" href="#"><span class="u_cbox_ico_bar"></span><span class="u_cbox_ico_report"></span><span class="u_cbox_in_report">신고</span></a></span></div><div class="u_cbox_tool"><a class="u_cbox_btn_reply" data-action="reply#toggle" data-log="RPC.replyopen#RPC.replyclose" data-param

...

[<div class="u_cbox_comment_box"><div class="u_cbox_area"><div class="u_cbox_info"><span class="u_cbox_info_main"><span class="u_cbox_name"><span class="u_cbox_name_area"><span class="u_cbox_nick_area"><span class="u_cbox_nick">dlgk****</span></span></span></span><button class="u_cbox_btn_totalcomment" data-action="userComment" data-log="RPC.ulist" data-param="objectId:'news018,0004504068',commentNo:1954810844,mine:false,open:true" type="button"><span class="u_cbox_txt_total">댓글모음</span><span class="u_cbox_ico_arrow"></span></button></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap"><span class="u_cbox_contents" data-lang="ko">새로운 기술개발과 상용화, 그리고 보급 기대합시다! 세상을 볼수있는 폭이 넓어지고 직접 경험하는것이 좋죠! 앞으로도 기대하겟습니다!</span></div><div class="u_cbox_info_base"><span class="u_cbox_date" data-value="2019-10-30T19:06:40+0900">2019.10.30. 19:06:40</span><span class="u_cbox_work_main"><a class="u_cbox_btn_report" data-action="blindReport#open" data-log="RPC.fold" data-param="195481

[]
[<div class="u_cbox_comment_box"><div class="u_cbox_area"><div class="u_cbox_info"><span class="u_cbox_info_main"><span class="u_cbox_name"><span class="u_cbox_name_area"><span class="u_cbox_nick_area"><span class="u_cbox_nick">trul****</span></span></span></span></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap"><span class="u_cbox_contents" data-lang="ko">가격만 싸다면 대박인듯.</span></div><div class="u_cbox_info_base"><span class="u_cbox_date" data-value="2019-10-30T17:53:17+0900">2019.10.30. 17:53:17</span><span class="u_cbox_work_main"><a class="u_cbox_btn_report" data-action="blindReport#open" data-log="RPC.fold" data-param="1912944482" href="#"><span class="u_cbox_ico_bar"></span><span class="u_cbox_ico_report"></span><span class="u_cbox_in_report">신고</span></a></span></div><div class="u_cbox_tool"><a class="u_cbox_btn_reply" data-action="reply#toggle" data-log="RPC.replyopen#RPC.replyclose" data-param="1912944482" href="#"><strong class="u_cbox_reply_txt"

[]
[]
[]
[]
[<div class="u_cbox_comment_box"><div class="u_cbox_area"><div class="u_cbox_info"><span class="u_cbox_info_main"><span class="u_cbox_name"><span class="u_cbox_name_area"><span class="u_cbox_nick_area"><span class="u_cbox_nick">ksj8****</span></span></span></span></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap"><span class="u_cbox_contents" data-lang="ko">보안에 힘쓰시길 하나 뚤리면 끝장임</span></div><div class="u_cbox_info_base"><span class="u_cbox_date" data-value="2019-10-30T12:07:33+0900">2019.10.30. 12:07:33</span><span class="u_cbox_work_main"><a class="u_cbox_btn_report" data-action="blindReport#open" data-log="RPC.fold" data-param="1912657712" href="#"><span class="u_cbox_ico_bar"></span><span class="u_cbox_ico_report"></span><span class="u_cbox_in_report">신고</span></a></span></div><div class="u_cbox_tool"><a class="u_cbox_btn_reply" data-action="reply#toggle" data-log="RPC.replyopen#RPC.replyclose" data-param="1912657712" href="#"><strong class="u_

[]


0  \
0                                             0   
0   sam9****</span></span></span></span></span>   
0   seou****</span></span></span></span></span>   
0          tecn****</span></span></span></span>   
0   jang****</span></span></span></span></span>   
0          kboy****</span></span></span></span>   
0          ahan****</span></span></span></span>   
0   park****</span></span></span></span></span>   
0   sa12****</span></span></span></span></span>   
0   ojyk****</span></span></span></span></span>   
0   1010****</span></span></span></span></span>   
0   ohru****</span></span></span></span></span>   
0   ss55****</span></span></span></span></span>   
0          king****</span></span></span></span>   
0          fafa****</span></span></span></span>   
0   art2****</span></span></span></span></span>   
0   mrtw****</span></span></span></span></span>   
0   kbh0****</span></span></span></span></span>   
0   chod****</span></span></span></span></span>   
0   chod****</span></span></span></span></span>   
0          jus_****</span></span></span></span>   
0   bull****</span></span></span></span></span>   
0          han5****</span></span></span></span>   
0   pich****</span></span></span></span></span>   
0   rmat****</span></span></span></span></span>   
0   hyos****</span></span></span></span></span>   
0   sim9****</span></span></span></span></span>   
0          onli****</span></span></span></span>   
0          kwak****</span></span></span></span>   
0   ndw8****</span></span></span></span></span>   
0   pluc****</span></span></span></span></span>   
0   k018****</span></span></span></span></span>   
0   shad****</span></span></span></span></span>   
0   toh0****</span></span></span></span></span>   
0   jhsh****</span></span></span></span></span>   
0          gap2****</span></span></span></span>   
0          jyh0****</span></span></span></span>   
0   ekwk****</span></span></span></span></span>   
0   2tae****</span></span></span></span></span>   
0   v020****</span></span></span></span></span>   
0          o_o_****</span></span></span></span>   
0   zhtj****</span></span></span></span></span>   
0   hjin****</span></span></span></span></span>   
0          soon****</span></span></span></span>   
0   tele****</span></span></span></span></span>   
0          chdg****</span></span></span></span>   
0   smsy****</span></span></span></span></span>   
0   comp****</span></span></span></span></span>   
0   inci****</span></span></span></span></span>   
0   foxj****</span></span></span></span></span>   
0   sam9****</span></span></span></span></span>   
0          777o****</span></span></span></span>   
0   p0re****</span></span></span></span></span>   
0   kimn****</span></span></span></span></span>   
0   g100****</span></span></span></span></span>   
0          ober****</span></span></span></span>   
0   lett****</span></span></span></span></span>   
0          djjs****</span></span></span></span>   
0          kd95****</span></span></span></span>   
0   lgan****</span></span></span></span></span>   
0   inyo****</span></span></span></span></span>   
0   kill****</span></span></span></span></span>   
0          nann****</span></span></span></span>   
0   qort****</span></span></span></span></span>   
0   sam9****</span></span></span></span></span>   
0   chlw****</span></span></span></span></span>   
0          casl****</span></span></span></span>   
0          brav****</span></span></span></span>   
0   yhk8****</span></span></span></span></span>   
0          mon5****</span></span></span></span>   
0   lang****</span></span></span></span></span>   
0   mira****</span></span></span></span></span>   
0   sens****</span></span></span></span></span>   
0          jjap****</span></span></span></span>   
0          hanb****</span></span></span></span>   
0          knh7****</span></span></span></span>   
0   leeb****</span></span></span></span></span>   
0   sam9****</span></span></span></span></span>   
0          good**

In [51]:
sitelist_comment = [sitelist_comment[0],sitelist_comment[1],sitelist_comment[2],sitelist_comment[3],sitelist_comment[4],sitelist_comment[5],sitelist_comment[6],sitelist_comment[7],sitelist_comment[8],sitelist_comment[9],sitelist_comment[10],sitelist_comment[11],sitelist_comment[12],sitelist_comment[13],sitelist_comment[14],sitelist_comment[15],sitelist_comment[16],sitelist_comment[17],sitelist_comment[18],sitelist_comment[19]]
sitelist_comment = [sitelist_comment[18]]
sitelist_comment

['https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=092&aid=0002173476']

In [ ]:
#cbox_module > div > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div
#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1953443284._user_id_no_ > div.u_cbox_comment_box > div

In [ ]:
globals()['Com_{}'.format(day)]

In [58]:
aaaa =pd.read_csv('Com_20191029.csv')
aaaa

0  \
0                                               0   
1            scvm****</span></span></span></span>   
2            mrme****</span></span></span></span>   
3     kinm****</span></span></span></span></span>   
4            dydg****</span></span></span></span>   
5     wlgn****</span></span></span></span></span>   
6     ndh4****</span></span></span></span></span>   
7            euls****</span></span></span></span>   
8     chba****</span></span></span></span></span>   
9     east****</span></span></span></span></span>   
10    swee****</span></span></span></span></span>   
11           panz****</span></span></span></span>   
12    geni****</span></span></span></span></span>   
13           naru****</span></span></span></span>   
14    choi****</span></span></span></span></span>   
15           hard****</span></span></span></span>   
16           toto****</span></span></span></span>   
17    zmal****</span></span></span></span></span>   
18    char****</span></span></span></span></span>   
19    tent****</span></span></span></span></span>   
20    tldu****</span></span></span></span></span>   
21           hong****</span></span></span></span>   
22    dbsr****</span></span></span></span></span>   
23    real****</span></span></span></span></span>   
24           bowe****</span></span></span></span>   
25    lapu****</span></span></span></span></span>   
26    deme****</span></span></span></span></span>   
27           able****</span></span></span></span>   
28    bkur****</span></span></span></span></span>   
29           7993****</span></span></span></span>   
30           amk1****</span></span></span></span>   
31           cjdw****</span></span></span></span>   
32    moon****</span></span></span></span></span>   
33    frim****</span></span></span></span></span>   
34    cyh3****</span></span></span></span></span>   
35    skyb****</span></span></span></span></span>   
36    yoon****</span></span></span></span></span>   
37    neo_****</span></span></span></span></span>   
38    sirs****</span></span></span></span></span>   
39    warp****</span></span></span></span></span>   
40    er20****</span></span></span></span></span>   
41    kind****</span></span></span></span></span>   
42    goal****</span></span></span></span></span>   
43           ion9****</span></span></span></span>   
44           ehdd****</span></span></span></span>   
45    puma****</span></span></span></span></span>   
46           22th****</span></span></span></span>   
47    cras****</span></span></span></span></span>   
48    lema****</span></span></span></span></span>   
49           nuli****</span></span></span></span>   
50           hong****</span></span></span></span>   
51    kooj****</span></span></span></span></span>   
52    kira****</span></span></span></span></span>   
53    care****</span></span></span></span></span>   
54           trya****</span></span></span></span>   
55    gene****</span></span></span></span></span>   
56    jiun****</span></span></span></span></span>   
57           cany****</span></span></span></span>   
58    sw11****</span></span></span></span></span>   
59    hqon****</span></span></span></span></span>   
60           nate****</span></span></span></span>   
61    jun_****</span></span></span></span></span>   
62    ahnz****</span></span></span></span></span>   
63    fore****</span></span></span></span></span>   
64    tont****</span></span></span></span></span>   
65    chri****</span></span></span></span></span>   
66    deme****</span></span></span></span></span>   
67           lson****</span></span></span></span>   
68    rick****</span></span></span></span></span>   
69    frms****</span></span></span></span></span>   
70    xs00****</span></span></span></span></span>   
71           sung****</span></span></span></span>   
72    lii3****</span></span></span></span></span>   
73    sese****</span></span></span></span></span>   
74    qora****</span></span></span></span></span>   
75    onyo****</span

In [ ]:
u_soup.

In [ ]:
#cbox_module > div > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more

In [ ]:
for i in range(-1) :
    print('a')

In [ ]:
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1898536955._user_id_no_ > div.u_cbox_comment_box.u_cbox_type_delete > div > div.u_cbox_info > span.u_cbox_info_main > span > span > span

In [ ]:
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_head > a > span.u_cbox_count

In [ ]:
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_head > a > span.u_cbox_count
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_head > a > span.u_cbox_count
#cbox_module > div > div.u_cbox_head > a > span.u_cbox_count
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_head > a > span.u_cbox_count
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_head > a > span.u_cbox_count
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_head > a > span.u_cbox_count

#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_head > a > span.u_cbox_count

In [ ]:
sitelist_sum

In [ ]:
p2.findall(str(aa[80]))+ p22.findall(str(aa[80]))[0][37:-68]
    p3.findall(str(aa[80]))[0][6:26]
    p4.findall(str(aa[96])) != [] #True 면 p5에서 값 아니면 Nan
    p5.findall(str(aa[80]))[0][23:-22]
    p6.findall(str(aa[96])) != []
    p7.findall(str(aa[80]))[0][30:-38]
    p8.findall(str(aa[80]))[0][42:-45]
c.findall(str(aa[80]))[0][1:-1] 


In [ ]:
sitelist_sum[51]

In [ ]:
sitelist_sum

In [ ]:
comment_date = pd.DataFrame(np.arange(6).reshape(1,-1), columns = ['ID','Comment','Write_time','Com-Com','Like','Dislike'])

In [ ]:
com_url = 'https://news.naver.com/main/read.nhn?mode=LS2D&mid=shm&sid1=105&sid2=731&oid=008&aid=0004280371'

In [ ]:
driver = webdriver.Chrome('chromedriver')
driver.get(com_url)

In [ ]:
com_soup = BeautifulSoup(driver.page_source, "lxml")

In [ ]:
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1923364224._user_id_no_ > div.u_cbox_reply_area > ul > li > div > div > div.u_cbox_text_wrap > span

In [ ]:
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()

In [ ]:
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()

In [ ]:
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()

In [ ]:
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()

In [ ]:
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()

In [ ]:
#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1864503222._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_text_wrap > span

In [ ]:
#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1864595942._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_text_wrap > span

In [ ]:
driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_favorite > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()

In [ ]:
com_select1 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_info > span.u_cbox_info_main > span > span > span')
com_select2 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_text_wrap > span')
com_select3 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_info_base > span.u_cbox_date')
com_select4 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_tool > a > span')
com_select5 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_recomm > em')
com_select6 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_unrecomm > em')
#1번 - 작성자 /2번 - 작성내용 /3번- 작성시간 /4번 -대댓글 수 /5번 - 좋아요 / 6번 - 싫어요


In [ ]:
com_select = com_select1 + com_select2 + com_select3 + com_select4 + com_select5 + com_select6

In [ ]:
com_select

In [ ]:
d = re.compile('>.*<')

In [ ]:
com_select_clean = [c.findall(str(com_select[0]))[0][1:-1] , d.findall(str(com_select[1]))[0][1:-1] , d.findall(str(com_select[2]))[0][1:-1], d.findall(str(com_select[3]))[0][1:-1], d.findall(str(com_select[4]))[0][1:-1], d.findall(str(com_select[5]))[0][1:-1]]

In [ ]:
com_select_clean

In [ ]:
com_select_np = np.array(com_select_clean).T

In [ ]:
df = pd.DataFrame(com_select_np).T
df.columns = ['ID','Comment','Write_time','Com-Com','Like','Dislike']

In [ ]:
comment_date = comment_date.append(df, ignore_index = True)

In [ ]:
comment_date

In [ ]:
sitelist_sum[0][:37] + 'm_view=1&includeAllCount=true&' + sitelist_sum[0][38:]

In [ ]:
sitelist_comment = []
for i in range(len(sitelist_sum)):
    sitelist_comment_temp = sitelist_sum[i][:37] + 'm_view=1&includeAllCount=true&' + sitelist_sum[i][38:]
    sitelist_comment.append(sitelist_comment_temp)
sitelist_comment

In [ ]:
com_url = 'https://news.naver.com/main/read.nhn?m_view=1&includeAllCount=true&ode=LS2D&mid=shm&sid1=105&sid2=731&oid=020&aid=0003244170'

In [ ]:
driver = webdriver.Chrome('chromedriver')
driver.get(com_url)

In [ ]:
com_soup = BeautifulSoup(driver.page_source, "lxml")

In [ ]:
c = re.compile('>\w+\W+<')

In [ ]:
cc = re.compile('>\w+<')

In [ ]:
d = re.compile('>.*<')

In [ ]:
e = re.compile('\w+\W+')

In [ ]:
f = re.compile('<.*span.*>')

In [ ]:
comment_many_temp = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_head > a > span.u_cbox_count')

In [ ]:
comment_many_temp

In [ ]:
comment_many = int(str(comment_many_temp[0])[27:-7])
comment_many

In [ ]:
int(comment_many / 20)

In [ ]:
for i in range(int(comment_many/20)):
    driver.find_element_by_css_selector("#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_paginate > a > span > span > span.u_cbox_page_more").click()
    sleep(1)

In [ ]:
com_soup = BeautifulSoup(driver.page_source, "lxml")

In [ ]:
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1923320274._user_id_no_ > div.u_cbox_comment_box > div

In [ ]:
bb = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1898536955._user_id_no_ > div.u_cbox_comment_box.u_cbox_type_delete > div')

In [ ]:
aa = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div')
aa[9]
c.findall(str(aa[9]))

In [ ]:
p1 = re.compile('<span class="u_cbox_nick">.*</span></span></span></span></span><span class="u_cbox_info_sub"></span></div><div class="u_cbox_text_wrap">')
p2 = re.compile('ass="u_cbox_contents" data-lang="ko">.*</span></div><div class="u_cbox_info_base"><span class="u_cbox_date"')
p22= re.compile('<span class="u_cbox_delete_contents">.*</span></div><div class="u_cbox_info_base"><span class="u_cbox_date"')
p3 = re.compile('0900">.*</span><span class=')
p4 = re.compile('<strong class="u_cbox_reply_txt">답글</strong><span class="u_cbox_reply')
p55 = re.compile('ass="u_cbox_reply_cnt">.*</span></a><div class=')
p5 = re.compile('u_cbox_reply_cnt u_vc">.*</span></a><div class=')
p6 = re.compile('<strong class="u_vc">공감/비공감</strong>')
p7 = re.compile('<em class="u_cbox_cnt_recomm">.*</em></a><a class="u_cbox_btn_unrecomm')
p8 = re.compile('비공감</span><em class="u_cbox_cnt_unrecomm">.*</em></a></div></div><span class="u_cbox_comm')

In [ ]:
aa = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div')

comm_df= pd.DataFrame(np.arange(6).reshape(1,-1))
for i in aa :
    
    templist = [0,0,0,0,0,0]
    templist[0] = c.findall(str(i))[0][1:-1] 
    templist[1] = (p2.findall(str(i))+ p22.findall(str(i)))[0][37:-68]
    templist[2] = p3.findall(str(i))[0][6:26]
    
    if p4.findall(str(i)) != []:
        templist[3] = (p55.findall(str(i)) + p5.findall(str(i)))[0][23:-22]
    else :
        templist[3] = 'Nan'
    if p6.findall(str(i)) != []:
        templist[4] = p7.findall(str(i))[0][30:-38]
        templist[5] = p8.findall(str(i))[0][42:-45]
    else:
        templist[4] = 'Nan'
        templist[5] = 'Nan'
    templist = np.array(templist)
    templist = pd.DataFrame(templist).T
    comm_df =comm_df.append(templist)
    
comm_df

In [ ]:
comm_df.shape

In [ ]:
comm_df.dtype

In [ ]:
aa[96]

In [ ]:
aa[1] = str(aa[1]).replace('</em></a></div></div><span class="u_cbox_comment_frame"><span class="u_cbox_ico_tip"></span><span class="u_cbox_comment_frame_top"><span class="u_cbox_comment_bg_r"></span><span class="u_cbox_comment_bg_l"></span></span><span class="u_cbox_comment_frame_bottom"><span class="u_cbox_comment_bg_r"></span><span class="u_cbox_comment_bg_l"></span></span></span>','')
p1.findall(aa[1])
aa[2]
qq =com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1923356114._user_id_no_ > div.u_cbox_comment_box.u_cbox_type_delete > div')
qq

In [ ]:
def com_crawl(com_soup) :
    com_select1 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_info > span.u_cbox_info_main > span > span > span > span')
    com_select2 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_text_wrap > span')
    com_select3 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_info_base > span.u_cbox_date')
    com_select4 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > a > span')
    com_select5 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_recomm > em')
    com_select6 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_unrecomm > em')
    
    com_select =pd.DataFrame(np.arange(6).reshape(1,-1), columns = ['ID','Comment','Write_time','ComCom','Like','Dislike'])
    com_select1_clean = c.findall(str(com_select1[:]))
    com_select1_clean =[i.replace('>','') for i in com_select1_clean]
    com_select1_clean =[i.replace('<','') for i in com_select1_clean]
    com_select2_clean = [str(i)[45:-7] for i in com_select2]
    com_select3_clean = [str(i)[64:-7] for i in com_select3]
    com_select4_clean = [d.findall(str(i)) for i in com_select4]
    com_select4_clean = [i[0][1] for i in com_select4_clean]
    com_select5_clean = [str(i)[30:-5] for i in com_select5]
    com_select6_clean = [str(i)[32:-5] for i in com_select6]
    temp1= pd.DataFrame(np.array(com_select1_clean))
    temp2 =pd.DataFrame(np.array(com_select2_clean))
    temp3 = pd.DataFrame(np.array(com_select3_clean))
    temp4 = pd.DataFrame(np.array(com_select4_clean))
    temp5 = pd.DataFrame(np.array(com_select5_clean))
    temp6 = pd.DataFrame(np.array(com_select6_clean))
    com_df= pd.concat([temp1,temp2,temp3,temp4,temp5,temp6],axis=1)
    com_df.columns = ['ID','text','Wtime','ComCom','Like','Dislike']
    return com_df
    
    

In [ ]:
com_select1 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_info > span.u_cbox_info_main > span > span > span > span')
com_select2 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_text_wrap > span')
com_select3 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_info_base > span.u_cbox_date')
com_select4 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > a > span')
com_select5 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_recomm > em')
com_select6 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_unrecomm > em')
com_select7 = com_soup.select('#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > a > strong')



com_select =pd.DataFrame(np.arange(6).reshape(1,-1), columns = ['ID','Comment','Write_time','ComCom','Like','Dislike'])
#com_select.ID  = np.array(com_select1).T#, np.array(com_select2).T # np.array(com_select3).T + np.array(com_select4).T + np.array(com_select5).T + np.arrary(com_select6).T
#com_select_clean = [c.findall(str(com_select[0]))[0][1:-1] , d.findall(str(com_select[1]))[0][1:-1] , d.findall(str(com_select[2]))[0][1:-1], d.findall(str(com_select[3]))[0][1:-1], d.findall(str(com_select[4]))[0][1:-1], d.findall(str(com_select[5]))[0][1:-1]]

com_select1_clean = c.findall(str(com_select1[:]))
com_select1_clean =[i.replace('>','') for i in com_select1_clean]
com_select1_clean =[i.replace('<','') for i in com_select1_clean]

com_select2_clean = [d.findall(str(i)) for i in com_select2]
com_select2_clean = [i[0][1:-1] for i in com_select2_clean]
com_select2_clean = [i for i in com_select2_clean if i != '']

com_select3_clean = [str(i)[64:-7] for i in com_select3]
com_select4_clean = [d.findall(str(i)) for i in com_select4]
com_select4_clean = [i[0][1] for i in com_select4_clean]
com_select5_clean = [str(i)[30:-5] for i in com_select5]
com_select6_clean = [str(i)[32:-5] for i in com_select6]

temp1= pd.DataFrame(np.array(com_select1_clean))
temp2 =pd.DataFrame(np.array(com_select2_clean))
temp3 = pd.DataFrame(np.array(com_select3_clean))
temp4 = pd.DataFrame(np.array(com_select4_clean))
temp5 = pd.DataFrame(np.array(com_select5_clean))
temp6 = pd.DataFrame(np.array(com_select6_clean))

#com_select.ID, com_select.Comment, com_select.Write_time, com_select.ComCom, com_select.Like, com_select.Dislike = temp1,temp2,temp3,temp4,temp5,temp6
com_df= pd.concat([temp1,temp2,temp3,temp4,temp5,temp6],axis=1)
com_df.columns = ['ID','text','Wtime','ComCom','Like','Dislike']
com_df
#len(com_select1_clean) , len(com_select2_clean)

In [ ]:
com_select4

In [ ]:
com_select2_clean = [d.findall(str(i)) for i in com_select2]
com_select2_clean2 = [i[0][1:-1] for i in com_select2_clean]
com_select2_clean2 = [i for i in com_select2_clean2 if i != '']
len(com_select2_clean2) 

In [ ]:
com_df2= pd.concat([temp1,temp2,temp3],axis=1)
com_df3= pd.concat([temp4, temp5, temp6], axis=1)

In [ ]:
c.findall(str(aa[0])) + cc.findall(str(aa[0])) + d.findall(str(aa[0]))

In [ ]:
aaa= re.sub(f,'',str(aa[0]))
aaa

In [ ]:
com_df[com_df.text =='']
com_df.loc[53:556]

In [ ]:
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_info > span.u_cbox_info_main > span > span > span > span
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_text_wrap > span
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_info_base > span.u_cbox_date

#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > a > span

#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_recomm > em
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_unrecomm > em

In [ ]:
com_select2 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_text_wrap > span')
    com_select3 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_info_base > span.u_cbox_date')
    com_select4 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_tool > a > span')
    com_select5 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_recomm > em')
    com_select6 = com_soup.select('#cbox_module > div > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1897594435._user_id_no_ > div.u_cbox_comment_box > div > div.u_cbox_tool > div > a.u_cbox_btn_unrecomm > em')
    com_select = com_select1 + com_select2 + com_select3 + com_select4 + com_select5 + com_select6

In [ ]:
#cbox_module > div.u_cbox_wrap.u_cbox_ko.u_cbox_type_sort_new > div.u_cbox_content_wrap > ul > li.u_cbox_comment.cbox_module__comment_1923364224._user_id_no_ > div.u_cbox_reply_area > ul > li > div > div > div.u_cbox_text_wrap > span